In [ ]:
!jupyter notebook --NotbookApp.iopub_Data_Rate_Limit=1e20

[I 2022-06-13 02:53:47.125 LabApp] JupyterLab extension loaded from /Users/neba/opt/anaconda3/lib/python3.8/site-packages/jupyterlab
[I 2022-06-13 02:53:47.125 LabApp] JupyterLab application directory is /Users/neba/opt/anaconda3/share/jupyter/lab
[I 02:53:47.130 NotebookApp] The port 8888 is already in use, trying another port.
[I 02:53:47.130 NotebookApp] The port 8889 is already in use, trying another port.
[I 02:53:47.131 NotebookApp] Serving notebooks from local directory: /Users/neba/Desktop/RUN_3
[I 02:53:47.131 NotebookApp] Jupyter Notebook 6.4.8 is running at:
[I 02:53:47.131 NotebookApp] http://localhost:8890/?token=fa3e8cfc6c16bc012deb0d9e48bf2bba425c1c27bbbe24bd
[I 02:53:47.131 NotebookApp]  or http://127.0.0.1:8890/?token=fa3e8cfc6c16bc012deb0d9e48bf2bba425c1c27bbbe24bd
[I 02:53:47.131 NotebookApp] Use Control-C to stop this server and shut down all kernels (twice to skip confirmation).
[C 02:53:47.144 NotebookApp] 
    
    To access the notebook, open this file in a brow

In [5]:
import os
os.chdir ("/Users/neba/Desktop/RUN_3/")
os.getcwd()
    
!pwd

/Users/neba/Desktop/RUN_3


In [4]:
!ls -lG


total 40
drwxr-xr-x  1126 neba  staff  36032 13 Jun 02:20 clean_fda
drwxr-xr-x   225 neba  staff   7200 12 Jun 23:37 cyclica_p1
-rw-r--r--     1 neba  staff   9579 13 Jun 01:13 pairwise_rmsd_12062022.ipynb
-rw-r--r--     1 neba  staff   8160 13 Jun 02:59 pairwise_rmsd_12062022_wellCommented.ipynb
drwxr-xr-x  1348 neba  staff  43136 13 Jun 02:25 test_run


In [ ]:
#!/usr/bin/python
#
# PairWise_RMSD_smalLigs.py
#For large throughput alignments, do not put script in thesame directory as pdb files
#Let directory of input files contain only the pdb files
#Use only "underscore" to name directories with >1 word. Do not use "stroks"
 
import __main__
__main__.pymol_argv = [ 'pymol', '-qc'] # Quiet and no GUI
 
import sys, time, os, re
from pymol import cmd
import pymol
import glob
import pandas as pd

import time
start_time = time.time()

pymol.finish_launching()

directory = "/Users/neba/Desktop/RUN_3/test_run/*.pdb"
#directory2 = "/Users/neba/Desktop/CyclicaVsFDA/Results/test1/*.pdb"


# Read User Input
structurePath = glob.glob(directory)
#structurePath2 = glob.glob(directory2)

structurePath.sort()
#structurePath2.sort()
extension = re.compile( '(^.*[\/]|\.(pdb|ent|brk))' )

object_list = []
for filename in structurePath:
    object_list.append(extension.sub ('',filename))

#for filename in structurePath2:
#object_list.append(extension.sub ('',filename))

rmsd = {}    
rmsd_list = []
for i in range (len(structurePath)):
    for j in range(1+i, len(structurePath)):
        obj_name1 = extension.sub('',structurePath[i].split("/")[-1].split(".")[0])
        cmd.load(structurePath[i],obj_name1)
        obj_name2 = extension.sub('',structurePath[j].split("/")[-1].split(".")[0])
        cmd.load(structurePath[j],obj_name2)
        
        rmsd_val = cmd.align(obj_name1, obj_name2, cycles=0, cutoff=5,
                            quiet=0, transform=0)#good ligand alignment when transform=0
                                                 #transform=0/1: do superposition {default: 1}
                             
        
        rmsd.setdefault(obj_name1,{})[obj_name2] = rmsd_val[0],rmsd_val[1],rmsd_val[2],
        rmsd_val[3], rmsd_val[4],rmsd_val[5], rmsd_val[6]
        
        rmsd_list.append((round(rmsd_val[3],2), round(rmsd_val[0],2), round(rmsd_val[4],2),
                          round(rmsd_val[5],2), obj_name1, obj_name2)) #indexing to creat
                                                                       #columns in df
             #columns in df
        
        #Delete object and replace with new items when 
        #loop loops through directory, the delete ccommnds must
        #align with loops for good results
       
        cmd.delete(obj_name2)
    cmd.delete(obj_name1)

#Re-order table
rmsd_list.sort()

#testing
print (rmsd_list)

#Create tables with poutput pairwise rmsds
rmsd_df = pd.DataFrame(rmsd_list)

#Renaming columns to match pymol's "align" column names
rmsd_df.columns = ['RMSD_BR','RMSD_AR', '#atomsAligned',
                   'Alignment_score','Ref_Ligand', 
                   'Aligned_Ligand']

#save file to directory
rmsd_df.to_csv("rmsd1115_working.csv", index=False)

rmsd_df.head(50)

#The "align" tool of pymol returns a list with 7 items:
#RMSD after refinement
#Number of aligned atoms after refinement
#Number of refinement cycles
#RMSD before refinement
#Number of aligned atoms before refinement
#Raw alignment score
#Number of residues aligned

#jupyter notebook --NotbookApp.iopub_Data_Rate_Limit=1e12





Cannot find license file.
 The license files (or license server system network addresses) attempted are 
listed below.  Use LM_LICENSE_FILE to use a different license file,
 or contact your software provider for a license file.
Feature:       PYMOL_MAIN
Filename:      /Library/Application Support/Schrodinger/licenses
License path:  /Library/Application Support/Schrodinger/licenses:
FlexNet Licensing error:-1,359.  System Error: 2 "No such file or directory"


 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 30 atoms aligned.
 Executive: RMSD =    3.315 (30 to 30 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 31 atoms aligned.
 Executive: RMSD =    3.300 (31 to 31 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 0.000
 ExecutiveAlign: 5 atoms aligned.
 Executive: RMSD =    2.265 (5 to 5 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 0.000
 ExecutiveAlign: 16 atoms aligned.
 Executive: RMSD =    2.796 (16 to 16 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score

 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 0.000
 ExecutiveAlign: 20 atoms aligned.
 Executive: RMSD =    3.468 (20 to 20 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 0.000
 ExecutiveAlign: 17 atoms aligned.
 Executive: RMSD =    2.804 (17 to 17 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 0.000
 ExecutiveAlign: 23 atoms aligned.
 Executive: RMSD =    4.541 (23 to 23 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 0.000
 ExecutiveAlign: 19 atoms aligned.
 Executive: RMSD =    3.302 (19 to 19 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: sc

 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 0.000
 ExecutiveAlign: 18 atoms aligned.
 Executive: RMSD =    3.947 (18 to 18 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 0.000
 ExecutiveAlign: 18 atoms aligned.
 Executive: RMSD =    3.062 (18 to 18 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 0.000
 ExecutiveAlign: 17 atoms aligned.
 Executive: RMSD =    2.852 (17 to 17 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 0.000
 ExecutiveAlign: 6 atoms aligned.
 Executive: RMSD =    2.029 (6 to 6 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score

 Executive: RMSD =    2.765 (17 to 17 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 0.000
 ExecutiveAlign: 22 atoms aligned.
 Executive: RMSD =    3.620 (22 to 22 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 0.000
 ExecutiveAlign: 22 atoms aligned.
 Executive: RMSD =    4.097 (22 to 22 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 0.000
 ExecutiveAlign: 20 atoms aligned.
 Executive: RMSD =    4.287 (20 to 20 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 0.000
 ExecutiveAlign: 10 atoms aligned.
 Executive: RMSD =    2.304 (10 to 10 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: 

...

 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 6 atoms aligned.
 Executive: RMSD =    1.380 (6 to 6 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 9 atoms aligned.
 Executive: RMSD =    4.361 (9 to 9 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 6 atoms aligned.
 Executive: RMSD =    1.268 (6 to 6 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 7 atoms aligned.
 Executive: RMSD =    2.168 (7 to 7 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 E

 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 6 atoms aligned.
 Executive: RMSD =    1.511 (6 to 6 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 8 atoms aligned.
 Executive: RMSD =    2.093 (8 to 8 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 9 atoms aligned.
 Executive: RMSD =    2.041 (9 to 9 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 9 atoms aligned.
 Executive: RMSD =    1.435 (9 to 9 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 E

 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 6 atoms aligned.
 Executive: RMSD =    3.221 (6 to 6 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 6 atoms aligned.
 Executive: RMSD =    3.226 (6 to 6 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 6 atoms aligned.
 Executive: RMSD =    3.763 (6 to 6 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 8 atoms aligned.
 Executive: RMSD =    2.705 (8 to 8 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 E

 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 6 atoms aligned.
 Executive: RMSD =    2.283 (6 to 6 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 9 atoms aligned.
 Executive: RMSD =    3.758 (9 to 9 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 6 atoms aligned.
 Executive: RMSD =    2.752 (6 to 6 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 9 atoms aligned.
 Executive: RMSD =    4.178 (9 to 9 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 E

 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 6 atoms aligned.
 Executive: RMSD =    1.179 (6 to 6 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 6 atoms aligned.
 Executive: RMSD =    1.313 (6 to 6 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 8 atoms aligned.
 Executive: RMSD =    2.632 (8 to 8 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 ExecutiveAlign: 6 atoms aligned.
 Executive: RMSD =    1.506 (6 to 6 atoms)
 Match: read scoring matrix.
 Match: assigning 1 x 1 pairwise scores.
 MatchAlign: aligning residues (1 vs 1)...
 MatchAlign: score 5.000
 E

In [ ]:
rmsd_df[(rmsd_df["RMSD_BR"] < 2) & (rmsd_df["Alignment_score"] > 3)
        & (rmsd_df['#atomsAligned'] > 5)].head(50)

In [ ]:
#import time for timing runs
import time
start_time = time.time()


In [ ]:
import numpy as np
import pandas as pd
import scanpy as sc
import anndata
from sklearn.decomposition import TruncatedSVD
import matplotlib
import matplotlib.pyplot as plt